In [1]:
import pandas as pd
import numpy as np
import os
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from math import sqrt
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error

In [2]:
train = pd.read_csv(os.path.join('data', 'clean_train.csv'))
test = pd.read_csv(os.path.join('data', 'clean_test.csv'))

In [3]:
train.head()

Unnamed: 0      PCA0      PCA1      PCA2      PCA3      PCA4      PCA5  \
0           0  4.345109  1.619386 -0.739617 -2.080179 -0.985088  1.999117   
1           1  0.019142 -3.106959  0.168223 -0.553341  0.940712  0.200719   
2           2  4.851149  1.242811 -0.351815 -1.484957 -0.758200  2.181179   
3           3 -1.771641  0.039500 -1.358623  1.920760 -2.550817  0.209519   
4           4  6.463747  1.064473  0.209472  0.448906 -1.555301  3.215822   

       PCA6      PCA7      PCA8  ...    PCA164    PCA165    PCA166    PCA167  \
0 -1.231870 -0.131782  1.316470  ...  0.160733  0.071333  0.155468  0.172801   
1 -0.468954  0.235082 -0.838022  ... -1.063234 -0.334556  0.361166 -1.218397   
2 -1.843949  0.296194  1.299142  ...  0.088334  0.238624  0.327280  0.325285   
3 -0.756387  0.700109 -1.408543  ... -0.172186 -0.518922  0.231498 -0.074296   
4 -0.946356 -0.805204  2.112526  ... -0.270189  0.375297 -0.396732 -0.109084   

     PCA168    PCA169    PCA170    PCA171  Id  SalePrice  
0 -0.169568 -0.144326  0.391713 -0.013357   1     208500  
1 -0.346191 -0.962753 -0.138863  1.083103   2     181500  
2 -0.704900 -0.036388 -0.540516  0.021711   3     223500  
3 -0.034287 -0.877735  0.028065 -0.321009   4     140000  
4  0.317305 -0.145975 -0.674692 -0.378458   5     250000  

[5 rows x 175 columns]

In [4]:
test.head()

Unnamed: 0      PCA0      PCA1      PCA2      PCA3      PCA4      PCA5  \
0           0 -3.208086 -2.987338 -0.327066 -1.609206  0.016879 -1.514939   
1           1 -1.403753 -4.261851  0.107527  0.935981  0.165777 -0.299485   
2           2  2.257002  0.427951 -0.610464 -1.301125 -1.058327  2.674177   
3           3  3.253618  0.537318 -0.796079 -0.851716 -1.209643  2.388795   
4           4  2.876409 -0.075909 -0.154959 -2.469870  1.407820  0.487532   

       PCA6      PCA7      PCA8  ...    PCA163    PCA164    PCA165    PCA166  \
0 -0.417889 -0.988173 -0.653363  ... -0.027364  0.653222 -0.201973 -0.769946   
1 -0.524918 -2.332121  0.031044  ...  3.856117  0.787996  0.215221  0.458275   
2 -1.500824 -0.223999  0.403440  ... -0.117138 -0.378473 -0.031613  0.090593   
3 -1.340676 -0.876322  0.421183  ... -0.441586  0.020066 -0.151709  0.444826   
4  0.072190  2.414446  1.667224  ...  0.269062  0.651172 -0.050461 -0.526448   

     PCA167    PCA168    PCA169    PCA170    PCA171    Id  
0 -0.344834  0.514257  1.114106  0.337765 -0.639617  1461  
1  1.135109  0.378972  0.953559 -1.008240  4.445435  1462  
2 -0.173914 -0.150098 -0.006612  0.190780 -0.152486  1463  
3  0.008218 -0.161705 -0.453482  0.472352  0.046141  1464  
4 -0.843701  0.574770 -0.227828  1.071423  1.362638  1465  

[5 rows x 174 columns]

In [5]:
# Set aside unnecessary features

trainId = train['Id'].astype(int)
testId = test['Id'].astype(int)

train = train.drop('Id', axis=1)
test = test.drop('Id', axis=1)

In [6]:
X = train.drop('SalePrice', axis=1)
y = train['SalePrice']
X_test = test

In [7]:
print(y)
print(X.shape)
print(X_test.shape)
X.head()

0       208500
1       181500
2       223500
3       140000
4       250000
         ...  
1455    175000
1456    210000
1457    266500
1458    142125
1459    147500
Name: SalePrice, Length: 1460, dtype: int64
(1460, 173)
(1459, 173)


Unnamed: 0      PCA0      PCA1      PCA2      PCA3      PCA4      PCA5  \
0           0  4.345109  1.619386 -0.739617 -2.080179 -0.985088  1.999117   
1           1  0.019142 -3.106959  0.168223 -0.553341  0.940712  0.200719   
2           2  4.851149  1.242811 -0.351815 -1.484957 -0.758200  2.181179   
3           3 -1.771641  0.039500 -1.358623  1.920760 -2.550817  0.209519   
4           4  6.463747  1.064473  0.209472  0.448906 -1.555301  3.215822   

       PCA6      PCA7      PCA8  ...    PCA162    PCA163    PCA164    PCA165  \
0 -1.231870 -0.131782  1.316470  ... -0.276936 -0.128260  0.160733  0.071333   
1 -0.468954  0.235082 -0.838022  ...  0.140974 -0.224535 -1.063234 -0.334556   
2 -1.843949  0.296194  1.299142  ... -0.289024 -0.282563  0.088334  0.238624   
3 -0.756387  0.700109 -1.408543  ...  0.286790  0.672251 -0.172186 -0.518922   
4 -0.946356 -0.805204  2.112526  ... -0.235585  0.019570 -0.270189  0.375297   

     PCA166    PCA167    PCA168    PCA169    PCA170    PCA171  
0  0.155468  0.172801 -0.169568 -0.144326  0.391713 -0.013357  
1  0.361166 -1.218397 -0.346191 -0.962753 -0.138863  1.083103  
2  0.327280  0.325285 -0.704900 -0.036388 -0.540516  0.021711  
3  0.231498 -0.074296 -0.034287 -0.877735  0.028065 -0.321009  
4 -0.396732 -0.109084  0.317305 -0.145975 -0.674692 -0.378458  

[5 rows x 173 columns]

In [8]:
# Initialize our models

tree_model = DecisionTreeRegressor()
rf_model = RandomForestRegressor()

In [9]:
# Fit our models to the training data

tree_model.fit(X, y)
rf_model.fit(X, y)

c:\users\tsb\appdata\local\programs\python\python37\lib\site-packages\sklearn\ensemble\forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)


RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
                      max_features='auto', max_leaf_nodes=None,
                      min_impurity_decrease=0.0, min_impurity_split=None,
                      min_samples_leaf=1, min_samples_split=2,
                      min_weight_fraction_leaf=0.0, n_estimators=10,
                      n_jobs=None, oob_score=False, random_state=None,
                      verbose=0, warm_start=False)

In [10]:
# Calculate error metrics for each model

tree_mse = mean_squared_error(y, tree_model.predict(X))
tree_mae = mean_absolute_error(y, tree_model.predict(X))
rf_mse = mean_squared_error(y, rf_model.predict(X))
rf_mae = mean_absolute_error(y, rf_model.predict(X))

In [11]:
print("Decision Tree training mse = ",tree_mse," & mae = ",tree_mae," & rmse = ", sqrt(tree_mse))
print("Random Forest training mse = ",rf_mse," & mae = ",rf_mae," & rmse = ", sqrt(rf_mse))

Decision Tree training mse =  0.0  & mae =  0.0  & rmse =  0.0
Random Forest training mse =  202420995.41813016  & mae =  8265.452260273973  & rmse =  14227.473261901783


In [15]:
# Setup and save Tree prediction

test_pred = tree_model.predict(X_test.values) # Note that we need to feed our model the values or our dataframe X_test
tree_predictions = np.c_[testId, test_pred] # Note that we take the argmax over the collumns to use our softmax output
tree_submission = pd.DataFrame(tree_predictions, columns = ['Id', 'SalePrice'])
tree_submission['Id'] = tree_submission['Id'].astype(int)
print(tree_submission.head)
tree_submission.to_csv("submissions/TreeSubmission.csv", index=False)

<bound method NDFrame.head of         Id  SalePrice
0     1461   125500.0
1     1462   149500.0
2     1463   185000.0
3     1464   201000.0
4     1465   176000.0
...    ...        ...
1454  2915    89000.0
1455  2916    80000.0
1456  2917   167900.0
1457  2918   135000.0
1458  2919   181000.0

[1459 rows x 2 columns]>


In [16]:
# Setup and save Random Forest prediction

test_pred = rf_model.predict(X_test.values) # Note that we need to feed our model the values or our dataframe X_test
rf_predictions = np.c_[testId, test_pred] # Note that we take the argmax over the collumns to use our softmax output
rf_submission = pd.DataFrame(rf_predictions, columns = ['Id', 'SalePrice'])
rf_submission['Id'] = rf_submission['Id'].astype(int)
print(rf_submission.head)
rf_submission.to_csv("submissions/RFSubmission.csv", index=False)

<bound method NDFrame.head of         Id  SalePrice
0     1461   136110.0
1     1462   167750.0
2     1463   184140.0
3     1464   186963.2
4     1465   188728.2
...    ...        ...
1454  2915    95030.0
1455  2916    99045.9
1456  2917   168480.0
1457  2918   114850.0
1458  2919   196190.0

[1459 rows x 2 columns]>


In [26]:
# Set up and save Ensemble prediction

ensemble_submission = tree_submission
ensemble_submission['TreeSalePrice'] = tree_submission['SalePrice']
ensemble_submission['ForestSalePrice'] = rf_submission['SalePrice']
ensemble_submission['SalePrice'] = ensemble_submission[['TreeSalePrice', 'ForestSalePrice']].mean(axis=1)
ensemble_submission = ensemble_submission.drop(['TreeSalePrice', 'ForestSalePrice'], axis=1)

In [27]:
ensemble_submission.head()

Id  SalePrice
0  1461  133457.50
1  1462  163187.50
2  1463  184355.00
3  1464  190472.40
4  1465  185546.15

In [28]:
ensemble_submission.to_csv("submissions/EnsembleSubmission.csv", index=False)